# Adatelőkészítés: megyei adatok

A KSH adatai alapján. Letöltés: 2019. május

In [1]:
import pandas as pd
import numpy as np
import re

In [2]:
def keep_county_or_capital(df, c="szintje"):
    '''Keep rows of df if iff df[c] is "főváros, régió" or "megye". Get rid of column c.'''
    return df[(df[c] == "főváros, régió") | (df[c] == "megye") | (df[c] == "megye, régió")].loc[:, [col for col in df.columns if col != c]]

In [3]:
def remove_whitespaces(x):
    return re.sub("\s", "", x)

## Adatok beimportálása

### Népesség adatok

In [4]:
nepesseg_014 = pd.read_excel("datain/6_1_2i-nepesseg-korcsoportszerint.xls", 
                             #header=[2], 
                             usecols="A:C,T",
                             skiprows=3, 
                             nrows=29)
nepesseg_014.columns=["neve", "szintje", "2001", "2018"]
nepesseg_014 = keep_county_or_capital(nepesseg_014)
nepesseg_014.columns = ["neve"] + list(map(lambda x: "lakónépesség_0-14_"+x, nepesseg_014.columns[1:]))
nepesseg_014.neve = nepesseg_014.neve.map(lambda x: remove_whitespaces(x))

In [5]:
nepesseg_1564 = pd.read_excel("datain/6_1_2i-nepesseg-korcsoportszerint.xls", 
                             #header=[2], 
                             usecols="A:C,T",
                             skiprows=3+30, 
                             nrows=29)
nepesseg_1564.columns=["neve", "szintje", "2001", "2018"]
nepesseg_1564 = keep_county_or_capital(nepesseg_1564)
nepesseg_1564.columns = ["neve"] + list(map(lambda x: "lakónépesség_15-64_"+x, nepesseg_1564.columns[1:]))
nepesseg_1564.neve = nepesseg_1564.neve.map(lambda x: remove_whitespaces(x))

In [6]:
nepesseg_65X = pd.read_excel("datain/6_1_2i-nepesseg-korcsoportszerint.xls", 
                             #header=[2], 
                             usecols="A:C,T",
                             skiprows=3+30+30, 
                             nrows=29)
nepesseg_65X.columns=["neve", "szintje", "2001", "2018"]
nepesseg_65X = keep_county_or_capital(nepesseg_65X)
nepesseg_65X.columns = ["neve"] + list(map(lambda x: "lakónépesség_65-_"+x, nepesseg_65X.columns[1:]))
nepesseg_65X.neve = nepesseg_65X.neve.map(lambda x: remove_whitespaces(x))

In [7]:
nepesseg = nepesseg_014
for df in [nepesseg_1564, nepesseg_65X]:
    nepesseg = nepesseg.merge(df, how='outer', on='neve', suffixes=['', '_Y'])
    for c in nepesseg.columns:
        if c != "neve":
            nepesseg[c] = nepesseg[c].astype('int')
        if c.endswith('_Y'):
            print("Deleting duplicate:", c)
            del nepesseg[c]
    

In [8]:
nepesseg["lakónépesség_arany_15-64_0-14_2001"] = nepesseg["lakónépesség_15-64_2001"] / nepesseg["lakónépesség_0-14_2001"]
nepesseg["lakónépesség_arany_15-64_65-_2001"]  = nepesseg["lakónépesség_15-64_2001"] / nepesseg["lakónépesség_65-_2001"]
nepesseg["lakónépesség_arany_15-64_0-14_2018"] = nepesseg["lakónépesség_15-64_2018"] / nepesseg["lakónépesség_0-14_2018"]
nepesseg["lakónépesség_arany_15-64_65-_2018"]  = nepesseg["lakónépesség_15-64_2018"] / nepesseg["lakónépesség_65-_2018"]

In [9]:
for c in set(map(lambda x: x[:-4], nepesseg.columns[1:])):
    nepesseg[c+"arany_2018_2001"] = nepesseg[c+"2018"] / nepesseg[c+"2001"]

In [10]:
np.shape(nepesseg)

(20, 16)

In [11]:
del nepesseg_014
del nepesseg_1564
del nepesseg_65X

### Népsűrűség, települések száma

In [12]:
nepsuruseg = pd.read_excel("datain/6_1_3i-nepsuruseg-telepulesekszama.xls", 
                             usecols="A:C,T",
                             skiprows=3, 
                             nrows=29)
nepsuruseg.columns=["neve", "szintje", "2001", "2018"]
nepsuruseg = keep_county_or_capital(nepsuruseg)
nepsuruseg.columns = ["neve"] + list(map(lambda x: "népsűrűség_fő_per_km2_"+x, nepsuruseg.columns[1:]))
nepsuruseg.neve = nepsuruseg.neve.map(lambda x: remove_whitespaces(x))

In [13]:
varosok = pd.read_excel("datain/6_1_3i-nepsuruseg-telepulesekszama.xls", 
                             usecols="A:C,T",
                             skiprows=3+30, 
                             nrows=29)
varosok.columns=["neve", "szintje", "2001", "2018"]
varosok = keep_county_or_capital(varosok)
varosok.columns = ["neve"] + list(map(lambda x: "városszám_"+x, varosok.columns[1:]))
for c in varosok.columns[1:]:
    varosok[c] = varosok[c].astype('int')
    
varosok.neve = varosok.neve.map(lambda x: remove_whitespaces(x))

In [14]:
kozsegek = pd.read_excel("datain/6_1_3i-nepsuruseg-telepulesekszama.xls", 
                             usecols="A:C,T",
                             skiprows=3+30+30, 
                             nrows=29)
kozsegek.columns=["neve", "szintje", "2001", "2018"]
kozsegek = keep_county_or_capital(kozsegek)
kozsegek.columns = ["neve"] + list(map(lambda x: "községszám_"+x, kozsegek.columns[1:]))
kozsegek.where(kozsegek != '–', other=0, inplace=True)
for c in kozsegek.columns[1:]:
    kozsegek[c] = kozsegek[c].astype('int')
    
kozsegek.neve = kozsegek.neve.map(lambda x: remove_whitespaces(x))

In [15]:
nepsuruseg_telepulesek = nepsuruseg
for df in [varosok, kozsegek]:
    nepsuruseg_telepulesek = nepsuruseg_telepulesek.merge(df, how='outer', on='neve', suffixes=['', '_Y'])
    for c in nepsuruseg_telepulesek.columns:
        if c.endswith('_Y'):
            print("Deleting duplicate:", c)
            del nepsuruseg_telepulesek[c]
    

In [16]:
for c in set(map(lambda x: x[:-4], nepsuruseg_telepulesek.columns[1:])):
    nepsuruseg_telepulesek[c+"arany_2018_2001"] = nepsuruseg_telepulesek[c+"2018"] / nepsuruseg_telepulesek[c+"2001"]

In [17]:
np.shape(nepsuruseg_telepulesek)

(20, 10)

In [18]:
del nepsuruseg
del varosok
del kozsegek

In [19]:
megyei_adatok = nepesseg.merge(nepsuruseg_telepulesek, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
    

In [20]:
del nepesseg
del nepsuruseg_telepulesek

### Várható élettartam, átlagéletkor

In [21]:
eletkor = pd.read_excel("datain/6_1_7i-atlageletkor.xls", 
                             usecols="A:C,E,F,H,I,K,L,N",
                             skiprows=4, 
                             nrows=29)
eletkor.columns=["neve", "szintje", "élettartam_ffi_2001", "élettartam_ffi_2017", "élettartam_nő_2001", "élettartam_nő_2017", "életkorátlag_ffi_2001", "életkorátlag_ffi_2018", "életkorátlag_nő_2001", "életkorátlag_nő_2018",]
eletkor = keep_county_or_capital(eletkor)
eletkor.neve = eletkor.neve.map(lambda x: remove_whitespaces(x))

In [22]:
for c in eletkor.columns:
    if c.endswith("2017"):
        col = c[:-4]
        eletkor[col+"arany_2017_2001"] = eletkor[c] / eletkor[col+"2001"]
    elif c.endswith("2018"):
        col = c[:-4]
        eletkor[col+"arany_2018_2001"] = eletkor[c] / eletkor[col+"2001"]

In [23]:
np.shape(eletkor)

(20, 13)

In [24]:
megyei_adatok = megyei_adatok.merge(eletkor, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
np.shape(megyei_adatok)

(20, 37)

In [25]:
del eletkor

### Átlagkereset

In [26]:
kereset = pd.read_excel("datain/6_2_1_16i-netto-atlagkereset.xls", 
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
kereset.columns=["neve", "szintje", "nettókereset_2001", "nettókereset_2017"]
kereset = keep_county_or_capital(kereset)
kereset["nettókereset_2001"] = kereset["nettókereset_2001"].astype('int')
kereset.neve = kereset.neve.map(lambda x: remove_whitespaces(x))

In [27]:
kereset["nettókereset_arany_2017_2001"] = kereset["nettókereset_2017"] / kereset["nettókereset_2001"]

In [28]:
megyei_adatok = megyei_adatok.merge(kereset, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
np.shape(megyei_adatok)

(20, 40)

In [29]:
del kereset

### Gazdasági aktivitás

In [30]:
aktivitas2006 = pd.read_excel("datain/6_2_1_1i-gazdasagi-aktivitas.xls", 
                             usecols="A,B,H:J",
                             skiprows=3, 
                             nrows=29)
aktivitas2006.columns=["neve", "szintje", "Munkanélküliségi ráta", "Aktivitási arány", "Foglalkoztatási ráta"]
aktivitas2006 = keep_county_or_capital(aktivitas2006)
aktivitas2006.neve = aktivitas2006.neve.map(lambda x: remove_whitespaces(x))

In [31]:
aktivitas2018 = pd.read_excel("datain/6_2_1_1i-gazdasagi-aktivitas.xls", 
                             usecols="A,B,H:J",
                             skiprows=375, 
                             nrows=29)
aktivitas2018.columns=["neve", "szintje", "Munkanélküliségi ráta", "Aktivitási arány", "Foglalkoztatási ráta"]
aktivitas2018 = keep_county_or_capital(aktivitas2018)
aktivitas2018.neve = aktivitas2018.neve.map(lambda x: remove_whitespaces(x))

In [32]:
aktivitas = aktivitas2006.merge(aktivitas2018, on='neve', how='outer', suffixes=["_2006", "_2018"] )

In [33]:
del aktivitas2006
del aktivitas2018

In [34]:
for c in ["Munkanélküliségi ráta", "Aktivitási arány", "Foglalkoztatási ráta"]:
    aktivitas[c + "_arany_2018_2006"] = aktivitas[c+"_2018"] / aktivitas[c+"_2006"]

In [35]:
megyei_adatok = megyei_adatok.merge(aktivitas, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
np.shape(megyei_adatok)

(20, 49)

In [36]:
del aktivitas

### Egy főre jutó bruttó hazai termék, ezer Ft

In [37]:
gdp = pd.read_excel("datain/6_3_1_2i-egy-fore-juto-hazai-termek.xls", 
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
gdp.columns=["neve", "szintje", "gdp_per_fo_ezerFt_2001", "gdp_per_fo_ezerFt_2017"]
gdp = keep_county_or_capital(gdp)
gdp.neve = gdp.neve.map(lambda x: remove_whitespaces(x))

In [38]:
gdp2 = pd.read_excel("datain/6_3_1_2i-egy-fore-juto-hazai-termek.xls", 
                             usecols="A,B,D,T",
                             skiprows=3+30, 
                             nrows=29)
gdp2.columns=["neve", "szintje", "gdp_orszagos_atlag_szazaleka_2001", "gdp_orszagos_atlag_szazaleka_2017"]
gdp2 = keep_county_or_capital(gdp2)
gdp2.neve = gdp2.neve.map(lambda x: remove_whitespaces(x))

In [39]:
gdp = gdp.merge(gdp2, on='neve', how='outer')

In [40]:
del gdp2

In [41]:
for c in ["gdp_per_fo_ezerFt", "gdp_orszagos_atlag_szazaleka"]:
    gdp[c + "_arany_2017_2001"] = gdp[c+"_2017"] / gdp[c+"_2001"]
np.shape(gdp)

(20, 7)

In [42]:
megyei_adatok = megyei_adatok.merge(gdp, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
np.shape(megyei_adatok)

(20, 55)

In [43]:
del gdp

### Az egy kiskereskedelmi üzletre jutó lakosok száma

In [44]:
kisker = pd.read_excel("datain/6_4_4_5i-kisker-uzlete-juto-lakosok-szama.xls",
                             usecols="A:E,AP:AR",
                             skiprows=3, 
                             nrows=29)
for c in kisker.columns[2:]:
    kisker[c] = (kisker[c].where(kisker[c] != '–', other=np.NaN)).astype('float')
kisker.columns=["neve", "szintje", "lakos_per_kiskerüzlet_összesen_2005", "lakos_per_kiskerüzlet_bevásárlóközpontokban_2005", "lakos_per_kiskerüzlet_hipermarketekben_2005", "lakos_per_kiskerüzlet_összesen_2018", "lakos_per_kiskerüzlet_bevásárlóközpontokban_2018", "lakos_per_kiskerüzlet_hipermarketekben_2018"]
kisker = keep_county_or_capital(kisker)
kisker.neve = kisker.neve.map(lambda x: remove_whitespaces(x))

/home/chell/anaconda3/envs/mlearn/lib/python3.6/site-packages/pandas/core/ops.py:1649: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


In [45]:
for c in kisker.columns:
    if c.endswith("2018"):
        col = c[:-4]
        kisker[col+"arany_2018_2005"] = kisker[c] / kisker[col+"2005"]

In [46]:
kisker.describe()

lakos_per_kiskerüzlet_összesen_2005  \
count                            20.000000   
mean                             65.890622   
std                               7.840840   
min                              49.653150   
25%                              61.278166   
50%                              65.198004   
75%                              69.486835   
max                              80.453043   

       lakos_per_kiskerüzlet_bevásárlóközpontokban_2005  \
count                                         16.000000   
mean                                        5093.648477   
std                                         2811.514367   
min                                          525.566698   
25%                                         3794.067584   
50%                                         4845.718804   
75%                                         5616.797391   
max                                        11312.000000   

       lakos_per_kiskerüzlet_hipermarketekben_2005  \
count                                    20.000000   
mean                                   8402.061883   
std                                    3730.967367   
min                                    3171.408219   
25%                                    6192.908744   
50%                                    7488.212465   
75%                                    9303.476847   
max                                   17902.000000   

       lakos_per_kiskerüzlet_összesen_2018  \
count                            20.000000   
mean                             77.500000   
std                               9.610849   
min                              62.000000   
25%                              69.750000   
50%                              78.000000   
75%                              84.000000   
max                              95.000000   

       lakos_per_kiskerüzlet_bevásárlóközpontokban_2018  \
count                                         19.000000   
mean                                        5690.631579   
std                                         9317.431127   
min                                          476.000000   
25%                                         2487.000000   
50%                                         4038.000000   
75%                                         5023.500000   
max                                        43600.000000   

       lakos_per_kiskerüzlet_hipermarketekben_2018  \
count                                    20.000000   
mean                                   4467.600000   
std                                    1336.770161   
min                                    2110.000000   
25%                                    3527.250000   
50%                                    4491.000000   
75%                                    5321.250000   
max                                    6827.000000   

       lakos_per_kiskerüzlet_összesen_arany_2018_2005  \
count                                       20.000000   
mean                                         1.179277   
std                                          0.096079   
min                                          0.998393   
25%                                          1.137082   
50%                                          1.176344   
75%                                          1.228098   
max                                          1.429919   

       lakos_per_kiskerüzlet_bevásárlóközpontokban_arany_2018_2005  \
count                                          16.000000             
mean                                            0.747311             
std                                             0.248981             
min                                             0.397606             
25%                                             0.515102             
50%                                             0.750412             
75%                                             0.924774             
max                                             1.171362         

In [47]:
kisker.loc[:, ["neve", "lakos_per_kiskerüzlet_bevásárlóközpontokban_2005", "lakos_per_kiskerüzlet_bevásárlóközpontokban_2018"]]

neve  lakos_per_kiskerüzlet_bevásárlóközpontokban_2005  \
0                 Budapest                                        525.566698   
1                     Pest                                       6223.462366   
3                    Fejér                                       5562.753247   
4        Komárom-Esztergom                                               NaN   
5                 Veszprém                                       5367.779412   
7        Győr-Moson-Sopron                                       2944.040000   
8                      Vas                                      11015.041667   
9                     Zala                                       4596.484375   
11                 Baranya                                       2329.561404   
12                  Somogy                                       5778.929825   
13                   Tolna                                               NaN   
16    Borsod-Abaúj-Zemplén                                       4077.410112   
17                   Heves                                               NaN   
18                  Nógrád                                               NaN   
20             Hajdú-Bihar                                       4638.618644   
21    Jász-Nagykun-Szolnok                                      11312.000000   
22  Szabolcs-Szatmár-Bereg                                       5165.830357   
24             Bács-Kiskun                                       2269.459916   
25                   Békés                                       4648.759036   
26                Csongrád                                       5042.678571   

    lakos_per_kiskerüzlet_bevásárlóközpontokban_2018  
0                                              476.0  
1                                             4992.0  
3                                             6516.0  
4                                             5642.0  
5                                             4429.0  
7                                             1521.0  
8                                             4792.0  
9                                             3573.0  
11                                            1667.0  
12                                            4181.0  
13                                           43600.0  
16                                            4038.0  
17                                            2757.0  
18                                               NaN  
20                                            2368.0  
21                                            5055.0  
22                                            5073.0  
24                                            2606.0  
25                                            2831.0  
26                                            2005.0

In [48]:
megyei_adatok = megyei_adatok.merge(kisker, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)

del kisker

In [49]:
np.shape(megyei_adatok)

(20, 64)

### A kereskedelmi szálláshelyeken eltöltött vendégéjszakák

In [50]:
szallas = pd.read_excel("datain/6_4_5_2i-szallashelyek-vendegforgalma.xls",
                             usecols="A,B,D,U",
                             skiprows=65, 
                             nrows=29)
szallas.columns=["neve", "szintje", "vendégéjszakák_2001", "vendégéjszakák_2018"]
szallas = keep_county_or_capital(szallas)
szallas.neve = szallas.neve.map(lambda x: remove_whitespaces(x))

In [51]:
szallas2 = pd.read_excel("datain/6_4_5_2i-szallashelyek-vendegforgalma.xls",
                             usecols="A,B,D,U",
                             skiprows=96, 
                             nrows=29)
szallas2.columns=["neve", "szintje", "vendégéjszakák_külföldi_2001", "vendégéjszakák_külföldi_2018"]
szallas2 = keep_county_or_capital(szallas2)
szallas2.neve = szallas2.neve.map(lambda x: remove_whitespaces(x))

In [52]:
szallas = szallas.merge(szallas2, on='neve')
del szallas2

In [53]:
for c in szallas.columns:
    if c.endswith("2018"):
        col = c[:-4]
        szallas[col+"arany_2018_2001"] = szallas[c] / szallas[col+"2001"]
        
np.shape(szallas)

(20, 7)

In [54]:
megyei_adatok = megyei_adatok.merge(szallas, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del szallas
np.shape(megyei_adatok)

(20, 70)

### Gépjárműállomány

In [55]:
szgk = pd.read_excel("datain/6_4_6_2i-gepjarmuallomany.xls",
                             usecols="A,B,D,U",
                             skiprows=36, 
                             nrows=29)
szgk.columns=["neve", "szintje", "Személygépkocsik_2001", "Személygépkocsik_2018"]
szgk = keep_county_or_capital(szgk)
szgk.neve = szgk.neve.map(lambda x: remove_whitespaces(x))

In [56]:
for c in szgk.columns:
    if c.endswith("2018"):
        col = c[:-4]
        szgk[col+"arany_2018_2001"] = szgk[c] / szgk[col+"2001"]
        
np.shape(szgk)

(20, 4)

In [57]:
megyei_adatok = megyei_adatok.merge(szgk, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del szgk
np.shape(megyei_adatok)

(20, 73)

### Internetkapcsolat

In [58]:
internet = pd.read_excel("datain/6_4_7_4_2i-internetes-elofizetesek-szama.xls",
                             usecols="A,B,D",
                             skiprows=3, 
                             nrows=29)
internet.columns=["neve", "szintje", "internet_összes_vezetékes_2017"]
internet = keep_county_or_capital(internet)
internet.neve = internet.neve.map(lambda x: remove_whitespaces(x))

In [59]:
internet2 = pd.read_excel("datain/6_4_7_4_2i-internetes-elofizetesek-szama.xls",
                             usecols="A,B,D",
                             skiprows=35, 
                             nrows=29)
internet2.columns=["neve", "szintje", "internet_vezetékes_DSL_2017"]
internet2 = keep_county_or_capital(internet2)
internet2.neve = internet2.neve.map(lambda x: remove_whitespaces(x))
internet = internet.merge(internet2, on='neve')
del internet2

In [60]:
internet2 = pd.read_excel("datain/6_4_7_4_2i-internetes-elofizetesek-szama.xls",
                             usecols="A,B,D",
                             skiprows=66, 
                             nrows=29)
internet2.columns=["neve", "szintje", "internet_vezetékes_kábeltévé_2017"]
internet2 = keep_county_or_capital(internet2)
internet2.neve = internet2.neve.map(lambda x: remove_whitespaces(x))
internet = internet.merge(internet2, on='neve')
del internet2

In [61]:
internet2 = pd.read_excel("datain/6_4_7_4_2i-internetes-elofizetesek-szama.xls",
                             usecols="A,B,D",
                             skiprows=97, 
                             nrows=29)
internet2.columns=["neve", "szintje", "internet_vezetékes_optikaikábel_2017"]
internet2 = keep_county_or_capital(internet2)
internet2.neve = internet2.neve.map(lambda x: remove_whitespaces(x))
internet = internet.merge(internet2, on='neve')
del internet2

In [62]:
np.shape(internet)

(20, 5)

In [63]:
megyei_adatok = megyei_adatok.merge(internet, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del internet
np.shape(megyei_adatok)

(20, 77)

### Gyógyszertárak száma

In [64]:
patika = pd.read_excel("datain/6_4_4_1i-kiskeruzletek-gyogyszertarak-szama.xls",
                             usecols="A,B,D,U",
                             skiprows=65, 
                             nrows=29)
patika.columns=["neve", "szintje", "gyógyszertárak_2001", "gyógyszertárak_2018"]
patika = keep_county_or_capital(patika)
patika.neve = patika.neve.map(lambda x: remove_whitespaces(x))

In [65]:
patika["gyógyszertárak_arány_2018_2001"] = patika.gyógyszertárak_2018 / patika.gyógyszertárak_2001
np.shape(patika)

(20, 4)

In [66]:
megyei_adatok = megyei_adatok.merge(patika, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del patika
np.shape(megyei_adatok)

(20, 80)

### Nonprofit szervezetek

In [67]:
nonprofit2005 = pd.read_excel("datain/6_3_2_7i-nonprofit-szervezetek.xls",
                             usecols="A,B,L:R",
                             skiprows=3, 
                             nrows=29)
nonprofit2005.columns=["neve", "szintje", "Összesen", "kultúra", "sport", "szabadidő", "oktatás", "szociális ellátás", "szakmai, gazdasági érdekképviselet"]
nonprofit2005 = keep_county_or_capital(nonprofit2005)
nonprofit2005.neve = nonprofit2005.neve.map(lambda x: remove_whitespaces(x))

In [68]:
nonprofit2017 = pd.read_excel("datain/6_3_2_7i-nonprofit-szervezetek.xls",
                             usecols="A,B,L:R",
                             skiprows=375, 
                             nrows=29)
nonprofit2017.columns=["neve", "szintje", "Összesen", "kultúra", "sport", "szabadidő", "oktatás", "szociális ellátás", "szakmai, gazdasági érdekképviselet"]
nonprofit2017 = keep_county_or_capital(nonprofit2017)
nonprofit2017.neve = nonprofit2017.neve.map(lambda x: remove_whitespaces(x))

In [69]:
nonprofit2005.columns = ["neve"] + list(map(lambda x: x+"_2005", nonprofit2005.columns[1:]))
nonprofit2017.columns = ["neve"] + list(map(lambda x: x+"_2017", nonprofit2017.columns[1:]))

In [70]:
nonprofit = nonprofit2005.merge(nonprofit2017, on='neve')

In [71]:
del nonprofit2005
del nonprofit2017

In [72]:
for c in nonprofit.columns:
    if c.endswith("2017"):
        col = c[:-4]
        nonprofit[col+"arany_2017_2005"] = nonprofit[c] / nonprofit[col+"2005"]
nonprofit.columns = ["neve"] + list(map(lambda x: "nonprofit_"+x, nonprofit.columns[1:]))
np.shape(nonprofit)

(20, 22)

In [73]:
megyei_adatok = megyei_adatok.merge(nonprofit, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del nonprofit
np.shape(megyei_adatok)

(20, 101)

### Bűnelkövetők

In [74]:
bunelkov = pd.read_excel("datain/6_2_7_3i-bunelkovetok.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
bunelkov.columns=["neve", "szintje", "bűnelkövetők_2001", "bűnelkövetők_2017"]
bunelkov = keep_county_or_capital(bunelkov)
bunelkov.neve = bunelkov.neve.map(lambda x: remove_whitespaces(x))

In [75]:
bunelkov2 = pd.read_excel("datain/6_2_7_3i-bunelkovetok.xls",
                             usecols="A,B,D,T",
                             skiprows=34, 
                             nrows=29)
bunelkov2.columns=["neve", "szintje", "bűnelkövetők_fiatalkorú_2001", "bűnelkövetők_fiatalkorú_2017"]
bunelkov2 = keep_county_or_capital(bunelkov2)
bunelkov2.neve = bunelkov2.neve.map(lambda x: remove_whitespaces(x))

In [76]:
bunelkov = bunelkov.merge(bunelkov2, on='neve', how='outer')

In [77]:
bunelkov["bűnelkövetők_arany_2017_2001"] = bunelkov["bűnelkövetők_2017"] / bunelkov["bűnelkövetők_2001"]
bunelkov["bűnelkövetők_fiatalkorú_arany_2017_2001"] = bunelkov["bűnelkövetők_fiatalkorú_2017"] / bunelkov["bűnelkövetők_fiatalkorú_2001"]
for c in ["_2001", "_2017"]:
    bunelkov["bűnelkövetők_arany_fiatalkorú_összes"+c] =  bunelkov["bűnelkövetők_fiatalkorú"+c]     / bunelkov["bűnelkövetők"+c]
bunelkov["bűnelkövetők_arany_összes_fiatalkorú_arany_2017_2001"] = bunelkov["bűnelkövetők_arany_fiatalkorú_összes_2017"] / bunelkov["bűnelkövetők_arany_fiatalkorú_összes_2001"] 
np.shape(bunelkov)

(20, 10)

In [78]:
megyei_adatok = megyei_adatok.merge(bunelkov, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del bunelkov
np.shape(megyei_adatok)

(20, 110)

### Bűncselekmények

In [79]:
buncsel = pd.read_excel("datain/6_2_7_1i-buncselekmenyek.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
buncsel.columns=["neve", "szintje", "bűncselekmények_2001", "bűncselekmények_2017"]
buncsel = keep_county_or_capital(buncsel)
buncsel.neve = buncsel.neve.map(lambda x: remove_whitespaces(x))

In [80]:
buncsel["bűncselekmények_arany_2017_2001"] = buncsel["bűncselekmények_2017"] / buncsel["bűncselekmények_2001"]
np.shape(buncsel)

(20, 4)

In [81]:
megyei_adatok = megyei_adatok.merge(buncsel, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del buncsel
np.shape(megyei_adatok)

(20, 113)

### Felsőfokú hallgatók száma

In [82]:
hallgatok = pd.read_excel("datain/6_2_5_4i-felsofoku-nappali-hallgato-lakhelyszerint.xls",
                             usecols="A,B,C,S",
                             skiprows=2, 
                             nrows=29)
hallgatok.columns=["neve", "szintje", "felsőfokúnappalihallgatók_2001", "felsőfokúnappalihallgatók_2017"]
hallgatok = keep_county_or_capital(hallgatok)
hallgatok.neve = hallgatok.neve.map(lambda x: remove_whitespaces(x))

In [83]:
hallgatok["felsőfokúnappalihallgatók_arany_2017_2001"] = hallgatok["felsőfokúnappalihallgatók_2017"] / hallgatok["felsőfokúnappalihallgatók_2001"]
np.shape(hallgatok)

(20, 4)

In [84]:
megyei_adatok = megyei_adatok.merge(hallgatok, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del hallgatok
np.shape(megyei_adatok)

(20, 116)

### Oktatás

#### Pedagógusok száma

In [85]:
pedagogusok = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
pedagogusok.columns=["neve", "szintje", "pedagógusok_óvodai_2001", "pedagógusok_óvodai_2017"]
pedagogusok = keep_county_or_capital(pedagogusok)
pedagogusok.neve = pedagogusok.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok.columns[1:]:
    pedagogusok[c] = pedagogusok[c].astype('int')
pedagogusok["pedagógusok_óvodai_arany_2017_2001"] = pedagogusok["pedagógusok_óvodai_2017"] / pedagogusok["pedagógusok_óvodai_2001"]

In [86]:
pedagogusok2 = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31, 
                             nrows=29)
pedagogusok2.columns=["neve", "szintje", "pedagógusok_áltisk_2001", "pedagógusok_áltisk_2017"]
pedagogusok2 = keep_county_or_capital(pedagogusok2)
pedagogusok2.neve = pedagogusok2.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok2.columns[1:]:
    pedagogusok2[c] = pedagogusok2[c].astype('int')
pedagogusok2["pedagógusok_áltisk_arany_2017_2001"] = pedagogusok2["pedagógusok_áltisk_2017"] / pedagogusok2["pedagógusok_áltisk_2001"]
pedagogusok = pedagogusok.merge(pedagogusok2, on='neve', how='outer')

In [87]:
pedagogusok2 = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31, 
                             nrows=29)
pedagogusok2.columns=["neve", "szintje", "pedagógusok_szakiskola_2001", "pedagógusok_szakiskola_2017"]
pedagogusok2 = keep_county_or_capital(pedagogusok2)
pedagogusok2.neve = pedagogusok2.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok2.columns[1:]:
    pedagogusok2[c] = pedagogusok2[c].astype('int')
pedagogusok2["pedagógusok_szakiskola_arany_2017_2001"] = pedagogusok2["pedagógusok_szakiskola_2017"] / pedagogusok2["pedagógusok_szakiskola_2001"]
pedagogusok = pedagogusok.merge(pedagogusok2, on='neve', how='outer')

In [88]:
pedagogusok2 = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31, 
                             nrows=29)
pedagogusok2.columns=["neve", "szintje", "pedagógusok_szakközépiskola_2001", "pedagógusok_szakközépiskola_2017"]
pedagogusok2 = keep_county_or_capital(pedagogusok2)
pedagogusok2.neve = pedagogusok2.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok2.columns[1:]:
    pedagogusok2[c] = pedagogusok2[c].astype('int')
pedagogusok2["pedagógusok_szakközépiskola_arany_2017_2001"] = pedagogusok2["pedagógusok_szakközépiskola_2017"] / pedagogusok2["pedagógusok_szakközépiskola_2001"]
pedagogusok = pedagogusok.merge(pedagogusok2, on='neve', how='outer')

In [89]:
pedagogusok2 = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31+31, 
                             nrows=29)
pedagogusok2.columns=["neve", "szintje", "pedagógusok_gimnázium_2001", "pedagógusok_gimnázium_2017"]
pedagogusok2 = keep_county_or_capital(pedagogusok2)
pedagogusok2.neve = pedagogusok2.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok2.columns[1:]:
    pedagogusok2[c] = pedagogusok2[c].astype('int')
pedagogusok2["pedagógusok_gimnázium_arany_2017_2001"] = pedagogusok2["pedagógusok_gimnázium_2017"] / pedagogusok2["pedagógusok_gimnázium_2001"]
pedagogusok = pedagogusok.merge(pedagogusok2, on='neve', how='outer')

In [90]:
pedagogusok2 = pd.read_excel("datain/6_2_5_2i-pedagogusok-szama.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31+31+31, 
                             nrows=29)
pedagogusok2.columns=["neve", "szintje", "pedagógusok_szakgimnázium_2001", "pedagógusok_szakgimnázium_2017"]
pedagogusok2 = keep_county_or_capital(pedagogusok2)
pedagogusok2.neve = pedagogusok2.neve.map(lambda x: remove_whitespaces(x))
for c in pedagogusok2.columns[1:]:
    pedagogusok2[c] = pedagogusok2[c].astype('int')
pedagogusok2["pedagógusok_szakgimnázium_arany_2017_2001"] = pedagogusok2["pedagógusok_szakgimnázium_2017"] / pedagogusok2["pedagógusok_szakgimnázium_2001"]
pedagogusok = pedagogusok.merge(pedagogusok2, on='neve', how='outer')

In [91]:
np.shape(pedagogusok)

(20, 19)

In [92]:
megyei_adatok = megyei_adatok.merge(pedagogusok, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
np.shape(megyei_adatok)

(20, 134)

In [93]:
del pedagogusok
del pedagogusok2

#### Köznevelési helyek

In [94]:
koznevint = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
koznevint.columns=["neve", "szintje", "köznevelési_intézmények_óvodai_2001", "köznevelési_intézmények_óvodai_2017"]
koznevint = keep_county_or_capital(koznevint)
koznevint.neve = koznevint.neve.map(lambda x: remove_whitespaces(x))
for c in koznevint.columns[1:]:
    koznevint[c] = koznevint[c].astype('int')
koznevint["köznevelési_intézmények_óvodai_arany_2017_2001"] = koznevint["köznevelési_intézmények_óvodai_2017"] / koznevint["köznevelési_intézmények_óvodai_2001"]

koznevint2 = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3+30, 
                             nrows=29)
koznevint2.columns=["neve", "szintje", "köznevelési_intézmények_áltisk_2001", "köznevelési_intézmények_áltisk_2017"]
koznevint2 = keep_county_or_capital(koznevint2)
for c in koznevint2.columns[1:]:
    koznevint2[c] = koznevint2[c].astype('int')
koznevint2.neve = koznevint2.neve.map(lambda x: remove_whitespaces(x))
koznevint2["köznevelési_intézmények_áltisk_arany_2017_2001"] = koznevint2["köznevelési_intézmények_áltisk_2017"] / koznevint2["köznevelési_intézmények_áltisk_2001"]
koznevint = koznevint.merge(koznevint2, on='neve')

koznevint2 = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31, 
                             nrows=29)
koznevint2.columns=["neve", "szintje", "köznevelési_intézmények_szakiskola_2001", "köznevelési_intézmények_szakiskola_2017"]
koznevint2 = keep_county_or_capital(koznevint2)
for c in koznevint2.columns[1:]:
    koznevint2[c] = koznevint2[c].astype('int')
koznevint2.neve = koznevint2.neve.map(lambda x: remove_whitespaces(x))
koznevint2["köznevelési_intézmények_szakiskola_arany_2017_2001"] = koznevint2["köznevelési_intézmények_szakiskola_2017"] / koznevint2["köznevelési_intézmények_szakiskola_2001"]
koznevint = koznevint.merge(koznevint2, on='neve')

koznevint2 = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31, 
                             nrows=29)
koznevint2.columns=["neve", "szintje", "köznevelési_intézmények_szakközépiskola_2001", "köznevelési_intézmények_szakközépiskola_2017"]
koznevint2 = keep_county_or_capital(koznevint2)
for c in koznevint2.columns[1:]:
    koznevint2[c] = koznevint2[c].astype('int')
koznevint2.neve = koznevint2.neve.map(lambda x: remove_whitespaces(x))
koznevint2["köznevelési_intézmények_szakközépiskola_arany_2017_2001"] = koznevint2["köznevelési_intézmények_szakközépiskola_2017"] / koznevint2["köznevelési_intézmények_szakközépiskola_2001"]
koznevint = koznevint.merge(koznevint2, on='neve')

koznevint2 = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31+31, 
                             nrows=29)
koznevint2.columns=["neve", "szintje", "köznevelési_intézmények_gimnázium_2001", "köznevelési_intézmények_gimnázium_2017"]
koznevint2 = keep_county_or_capital(koznevint2)
for c in koznevint2.columns[1:]:
    koznevint2[c] = koznevint2[c].astype('int')
koznevint2.neve = koznevint2.neve.map(lambda x: remove_whitespaces(x))
koznevint2["köznevelési_intézmények_gimnázium_arany_2017_2001"] = koznevint2["köznevelési_intézmények_gimnázium_2017"] / koznevint2["köznevelési_intézmények_gimnázium_2001"]
koznevint = koznevint.merge(koznevint2, on='neve')

koznevint2 = pd.read_excel("datain/6_2_5_1i-koznevelesi-feladatellatasihely.xls",
                             usecols="A,B,D,T",
                             skiprows=3+31+31+31+31+31, 
                             nrows=29)
koznevint2.columns=["neve", "szintje", "köznevelési_intézmények_szakgimnázium_2001", "köznevelési_intézmények_szakgimnázium_2017"]
koznevint2 = keep_county_or_capital(koznevint2)
for c in koznevint2.columns[1:]:
    koznevint2[c] = koznevint2[c].astype('int')
koznevint2.neve = koznevint2.neve.map(lambda x: remove_whitespaces(x))
koznevint2["köznevelési_intézmények_szakgimnázium_arany_2017_2001"] = koznevint2["köznevelési_intézmények_szakgimnázium_2017"] / koznevint2["köznevelési_intézmények_szakgimnázium_2001"]
koznevint = koznevint.merge(koznevint2, on='neve')

print(np.shape(koznevint))

(20, 19)


In [95]:
megyei_adatok = megyei_adatok.merge(koznevint, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del koznevint
del koznevint2

np.shape(megyei_adatok)

(20, 152)

### Szociális étkeztetésben részesülők

In [96]:
szocel = pd.read_excel("datain/6_2_4_6i-szocialis-ellatottak.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
szocel.columns=["neve", "szintje", "szociális_étkeztetésben_részesülők_2001", "szociális_étkeztetésben_részesülők_2018"]
szocel = keep_county_or_capital(szocel)
for c in szocel.columns[1:]:
    szocel[c] = szocel[c].astype('int')
szocel.neve = szocel.neve.map(lambda x: remove_whitespaces(x))
szocel["szociális_étkeztetésben_részesülők_arany_2018_2001"] = szocel["szociális_étkeztetésben_részesülők_2018"] / szocel["szociális_étkeztetésben_részesülők_2001"]
np.shape(szocel)

(20, 4)

In [97]:
megyei_adatok = megyei_adatok.merge(szocel, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del szocel
np.shape(megyei_adatok)

(20, 155)

### Hátrányos helyzetű gyermekek

In [98]:
hh = pd.read_excel("datain/6_2_4_3i-hatranyos-kiskoruak.xls",
                             usecols="A,B,C,G",
                             skiprows=3, 
                             nrows=29)
hh.columns=["neve", "szintje", "hátrányoshelyzetű_kiskorúak_2013", "hátrányoshelyzetű_kiskorúak_2017"]
hh = keep_county_or_capital(hh)
hh.neve = hh.neve.map(lambda x: remove_whitespaces(x))
hh["hátrányoshelyzetű_kiskorúak_arany_2017_2013"] = hh["hátrányoshelyzetű_kiskorúak_2017"] / hh["hátrányoshelyzetű_kiskorúak_2013"]

In [99]:
hh2 = pd.read_excel("datain/6_2_4_3i-hatranyos-kiskoruak.xls",
                             usecols="A,B,C,G",
                             skiprows=3+30, 
                             nrows=29)
hh2.columns=["neve", "szintje", "hátrányoshelyzetű_halmozottan_kiskorúak_2013", "hátrányoshelyzetű_halmozottan_kiskorúak_2017"]
hh2 = keep_county_or_capital(hh2)
hh2.neve = hh2.neve.map(lambda x: remove_whitespaces(x))
hh2["hátrányoshelyzetű_halmozottan_kiskorúak_arany_2017_2013"] = hh2["hátrányoshelyzetű_halmozottan_kiskorúak_2017"] / hh2["hátrányoshelyzetű_halmozottan_kiskorúak_2013"]
hh = hh.merge(hh2, on='neve')

In [100]:
np.shape(hh)

(20, 7)

In [101]:
megyei_adatok = megyei_adatok.merge(hh, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del hh
del hh2
np.shape(megyei_adatok)

(20, 161)

### Orvosok száma

In [102]:
orvosok = pd.read_excel("datain/6_2_3_1i-dolgozo-orvosok.xls",
                             usecols="A,B,C,R",
                             skiprows=3, 
                             nrows=29)
orvosok.columns=["neve", "szintje", "orvosok_száma_2002", "orvosok_száma_2017"]
orvosok = keep_county_or_capital(orvosok)
orvosok.neve = orvosok.neve.map(lambda x: remove_whitespaces(x))
orvosok["orvosok_száma_arany_2017_2002"] = orvosok["orvosok_száma_2017"] / orvosok["orvosok_száma_2002"]

orvosok2 = pd.read_excel("datain/6_2_3_1i-dolgozo-orvosok.xls",
                             usecols="A,B,C,R",
                             skiprows=3+30, 
                             nrows=29)
orvosok2.columns=["neve", "szintje", "orvosok_tízezer_lakosra_2002", "orvosok_tízezer_lakosra_2017"]
orvosok2 = keep_county_or_capital(orvosok2)
orvosok2.neve = orvosok2.neve.map(lambda x: remove_whitespaces(x))
orvosok2["orvosok_tízezer_lakosra_arany_2017_2002"] = orvosok2["orvosok_tízezer_lakosra_2017"] / orvosok2["orvosok_tízezer_lakosra_2002"]
orvosok = orvosok.merge(orvosok2, on='neve')
np.shape(orvosok)

(20, 7)

In [103]:
megyei_adatok = megyei_adatok.merge(orvosok, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del orvosok
del orvosok2
np.shape(megyei_adatok)

(20, 167)

### Gáz, villany fogyasztás

In [104]:
fogyasztas = pd.read_excel("datain/6_2_2_7i-gaz-villany-fogyasztas.xls",
                             usecols="A,B,D,T",
                             skiprows=3, 
                             nrows=29)
fogyasztas.columns=["neve", "szintje", "háztartás_gázfogyasztás_m3_2001", "háztartás_gázfogyasztás_m3_2017"]
fogyasztas = keep_county_or_capital(fogyasztas)
fogyasztas.neve = fogyasztas.neve.map(lambda x: remove_whitespaces(x))
fogyasztas["háztartás_gázfogyasztás_m3_arany_2017_2001"] = fogyasztas["háztartás_gázfogyasztás_m3_2017"] / fogyasztas["háztartás_gázfogyasztás_m3_2001"]

fogyasztas2 = pd.read_excel("datain/6_2_2_7i-gaz-villany-fogyasztas.xls",
                             usecols="A,B,D,T",
                             skiprows=3+30, 
                             nrows=29)
fogyasztas2.columns=["neve", "szintje", "háztartás_áramfogyasztás_kwh_2001", "háztartás_áramfogyasztás_kwh_2017"]
fogyasztas2 = keep_county_or_capital(fogyasztas2)
fogyasztas2.neve = fogyasztas2.neve.map(lambda x: remove_whitespaces(x))
fogyasztas2["háztartás_áramfogyasztás_kwh_arany_2017_2001"] = fogyasztas2["háztartás_áramfogyasztás_kwh_2017"] / fogyasztas2["háztartás_áramfogyasztás_kwh_2001"]
fogyasztas = fogyasztas.merge(fogyasztas2, on='neve')
np.shape(fogyasztas)

(20, 7)

In [105]:
megyei_adatok = megyei_adatok.merge(fogyasztas, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del fogyasztas
del fogyasztas2
np.shape(megyei_adatok)

(20, 173)

### Közműolló

In [106]:
kozmuollo = pd.read_excel("datain/6_2_2_6i-kozmuollo.xls",
                             usecols="A,B,D,T",
                             skiprows=3+30, 
                             nrows=29)
kozmuollo.columns=["neve", "szintje", "közműolló_csatornázott_lakások_vízközművezettek_százalékában_2001", "közműolló_csatornázott_lakások_vízközművezettek_százalékában_2017"]
kozmuollo = keep_county_or_capital(kozmuollo)
kozmuollo.neve = kozmuollo.neve.map(lambda x: remove_whitespaces(x))
kozmuollo["közműolló_csatornázott_lakások_vízközművezettek_százalékában_arany_2017_2001"] = kozmuollo["közműolló_csatornázott_lakások_vízközművezettek_százalékában_2017"] / kozmuollo["közműolló_csatornázott_lakások_vízközművezettek_százalékában_2001"]
np.shape(kozmuollo)

(20, 4)

In [107]:
megyei_adatok = megyei_adatok.merge(kozmuollo, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del kozmuollo
np.shape(megyei_adatok)

(20, 176)

### Építési engedélyek

In [108]:
epitesieng = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3, 
                             nrows=29)
epitesieng.columns=["neve", "szintje", "építési_engedélyek_lakóépületek_2003", "építési_engedélyek_lakóépületek_2018"]
epitesieng = keep_county_or_capital(epitesieng)
epitesieng.neve = epitesieng.neve.map(lambda x: remove_whitespaces(x))
epitesieng["építési_engedélyek_lakóépületek_arany_2018_2003"] = epitesieng["építési_engedélyek_lakóépületek_2018"] / epitesieng["építési_engedélyek_lakóépületek_2003"]

epitesieng2 = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3+31, 
                             nrows=29)
epitesieng2.columns=["neve", "szintje", "építési_engedélyek_lakóépület_terület_ezer_m2_2003", "építési_engedélyek_lakóépület_terület_ezer_m2_2018"]
epitesieng2 = keep_county_or_capital(epitesieng2)
epitesieng2.neve = epitesieng2.neve.map(lambda x: remove_whitespaces(x))
epitesieng2["építési_engedélyek_lakóépület_terület_ezer_m2_arany_2018_2003"] = epitesieng2["építési_engedélyek_lakóépület_terület_ezer_m2_2018"] / epitesieng2["építési_engedélyek_lakóépület_terület_ezer_m2_2003"]
epitesieng = epitesieng.merge(epitesieng2, on='neve')

epitesieng2 = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3+31+31, 
                             nrows=29)
epitesieng2.columns=["neve", "szintje", "építési_engedélyek_lakóépületek_egylakásos_2003", "építési_engedélyek_lakóépületek_egylakásos_2018"]
epitesieng2 = keep_county_or_capital(epitesieng2)
epitesieng2.neve = epitesieng2.neve.map(lambda x: remove_whitespaces(x))
epitesieng2["építési_engedélyek_lakóépületek_egylakásos_arany_2018_2003"] = epitesieng2["építési_engedélyek_lakóépületek_egylakásos_2018"] / epitesieng2["építési_engedélyek_lakóépületek_egylakásos_2003"]
epitesieng = epitesieng.merge(epitesieng2, on='neve')

epitesieng2 = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3+31+31+31, 
                             nrows=29)
epitesieng2.columns=["neve", "szintje", "építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_2003", "építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_2018"]
epitesieng2 = keep_county_or_capital(epitesieng2)
epitesieng2.neve = epitesieng2.neve.map(lambda x: remove_whitespaces(x))
epitesieng2["építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_arany_2018_2003"] = epitesieng2["építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_2018"] / epitesieng2["építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_2003"]
epitesieng = epitesieng.merge(epitesieng2, on='neve')

epitesieng2 = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3+31+31+31+31, 
                             nrows=29)
epitesieng2.columns=["neve", "szintje", "építési_engedélyek_nem_lakóépület_2003", "építési_engedélyek_nem_lakóépület_2018"]
epitesieng2 = keep_county_or_capital(epitesieng2)
epitesieng2.neve = epitesieng2.neve.map(lambda x: remove_whitespaces(x))
epitesieng2["építési_engedélyek_nem_lakóépület_arany_2018_2003"] = epitesieng2["építési_engedélyek_nem_lakóépület_2018"] / epitesieng2["építési_engedélyek_nem_lakóépület_2003"]
epitesieng = epitesieng.merge(epitesieng2, on='neve')

epitesieng2 = pd.read_excel("datain/6_2_2_3i-epitesi-engedelyek.xls",
                             usecols="A,B,C,R",
                             skiprows=3+31+31+31+31+31, 
                             nrows=29)
epitesieng2.columns=["neve", "szintje", "építési_engedélyek_nem_lakóépület_terület_ezer_m2_2003", "építési_engedélyek_nem_lakóépület_terület_ezer_m2_2018"]
epitesieng2 = keep_county_or_capital(epitesieng2)
epitesieng2.neve = epitesieng2.neve.map(lambda x: remove_whitespaces(x))
epitesieng2["építési_engedélyek_nem_lakóépület_terület_ezer_m2_arany_2018_2003"] = epitesieng2["építési_engedélyek_nem_lakóépület_terület_ezer_m2_2018"] / epitesieng2["építési_engedélyek_nem_lakóépület_terület_ezer_m2_2003"]
epitesieng = epitesieng.merge(epitesieng2, on='neve')
np.shape(epitesieng)

(20, 19)

In [109]:
for c in epitesieng.columns:
    if (c!='neve') and ("terület" not in c) and ("_arany_" not in c):
        epitesieng[c] = epitesieng[c].astype('int')

In [110]:
megyei_adatok = megyei_adatok.merge(epitesieng, how='outer', on='neve', suffixes=['', '_Y'])
for c in megyei_adatok.columns:
    if c.endswith('_Y'):
        print("Duplicate column:", c)
        
del epitesieng
del epitesieng2
np.shape(megyei_adatok)

(20, 194)

## Megyei adatok

In [111]:
megyei_adatok.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 20 entries, 0 to 19
Columns: 194 entries, neve to építési_engedélyek_nem_lakóépület_terület_ezer_m2_arany_2018_2003
dtypes: float64(109), int64(84), object(1)
memory usage: 30.5+ KB


In [112]:
for c in megyei_adatok.columns:
    if len(megyei_adatok[c].dropna()) != 20:
        print(c)

községszám_arany_2018_2001
lakos_per_kiskerüzlet_bevásárlóközpontokban_2005
lakos_per_kiskerüzlet_bevásárlóközpontokban_2018
lakos_per_kiskerüzlet_bevásárlóközpontokban_arany_2018_2005


In [113]:
megyei_adatok

neve  lakónépesség_0-14_2001  lakónépesség_0-14_2018  \
0                 Budapest                  226546                  236591   
1                     Pest                  189764                  211624   
2                    Fejér                   74418                   60574   
3        Komárom-Esztergom                   53788                   43600   
4                 Veszprém                   62531                   47646   
5        Győr-Moson-Sopron                   69288                   68452   
6                      Vas                   43431                   33550   
7                     Zala                   46955                   34753   
8                  Baranya                   65908                   50191   
9                   Somogy                   56790                   41137   
10                   Tolna                   42535                   30249   
11    Borsod-Abaúj-Zemplén                  142631                  102166   
12                   Heves                   53503                   42207   
13                  Nógrád                   37054                   26462   
14             Hajdú-Bihar                  102844                   79373   
15    Jász-Nagykun-Szolnok                   73914                   54246   
16  Szabolcs-Szatmár-Bereg                  120447                   88932   
17             Bács-Kiskun                   93876                   72446   
18                   Békés                   66711                   43623   
19                Csongrád                   69063                   54094   

    lakónépesség_15-64_2001  lakónépesség_15-64_2018  lakónépesség_65-_2001  \
0                   1219448                  1161897                 313215   
1                    741430                   838010                 140704   
2                    295874                   279871                  57823   
3                    219803                   199417                  43407   
4                    259311                   226615                  53775   
5                    301745                   311916                  63176   
6                    184698                   170405                  41020   
7                    205578                   178550                  47963   
8                    281500                   241350                  60739   
9                    229096                   200064                  52044   
10                   170623                   144711                  38436   
11                   502438                   428836                 108428   
12                   220277                   193144                  53953   
13                   149465                   125490                  35086   
14                   374902                   357016                  75518   
15                   281410                   244086                  65137   
16                   393490                   381403                  76052   
17                   369340                   333847                  84738   
18                   268301                   222337                  66907   
19                   294592                   265525                  66859   

    lakónépesség_65-_2018  lakónépesség_arany_15-64_0-14_2001  \
0                  351246                            5.382783   
1                  212230                            3.907116   
2                   76246                            3.975839   
3                   54437                            4.086469   
4                   67164                            4.146919   
5                   81150                            4.354939   
6                   49350                            4.252677   
7                   57331                            4.378192   
8                   72180                            4.271105   
9                   62601                            4.034091   
10      

In [114]:
megyei_adatok.describe()

lakónépesség_0-14_2001  lakónépesség_0-14_2018  \
count               20.000000               20.000000   
mean             84599.850000            71095.800000   
std              50242.418152            56102.456537   
min              37054.000000            26462.000000   
25%              53716.750000            41939.500000   
50%              67887.000000            52142.500000   
75%              96118.000000            74177.750000   
max             226546.000000           236591.000000   

       lakónépesség_15-64_2001  lakónépesség_15-64_2018  \
count             2.000000e+01             2.000000e+01   
mean              3.481660e+05             3.252245e+05   
std               2.446057e+05             2.496916e+05   
min               1.494650e+05             1.254900e+05   
25%               2.201585e+05             1.978488e+05   
50%               2.814550e+05             2.427180e+05   
75%               3.707305e+05             3.396392e+05   
max               1.219448e+06             1.161897e+06   

       lakónépesség_65-_2001  lakónépesség_65-_2018  \
count              20.000000               20.00000   
mean            77249.000000            92598.25000   
std             60817.858389            71083.46863   
min             35086.000000            38985.00000   
25%             51023.750000            59663.50000   
50%             61957.500000            72559.50000   
75%             75651.500000            89538.25000   
max            313215.000000           351246.00000   

       lakónépesség_arany_15-64_0-14_2001  lakónépesség_arany_15-64_65-_2001  \
count                           20.000000                          20.000000   
mean                             4.070809                           4.570819   
std                              0.415242                           0.399741   
min                              3.266914                           3.893326   
25%                              3.927533                           4.311754   
50%                              4.033899                           4.470889   
75%                              4.255896                           4.857712   
max                              5.382783                           5.269431   

       lakónépesség_arany_15-64_0-14_2018  lakónépesség_arany_15-64_65-_2018  \
count                           20.000000                          20.000000   
mean                             4.673321                           3.473271   
std                              0.302104                           0.322223   
min                              3.959901                           3.085229   
25%                              4.542437                           3.251545   
50%                              4.681294                           3.354070   
75%                              4.874666                           3.665105   
max                              5.137686                           4.332845   

       ...  építési_engedélyek_lakóépületek_egylakásos_arany_2018_2003  \
count  ...                                          20.000000            
mean   ...                                           0.395314            
std    ...                                           0.185105            
min    ...                                           0.155136            
25%    ...                                           0.227333            
50%    ...                                           0.359839            
75%    ...                                           0.536791            
max    ...                                           0.812456            

       építési_engedélyek_lakóépületek_egylakásos_terület_ezer_m2_2003  \
count                                          20.000000                 
mean                                          153.530000                 
std                                           155.072981                 
min                                            39.800000    

## Exportálás

Átnevezések exportálás előtt

In [115]:
megyei_adatok.rename(columns={'neve': 'megye'}, inplace=True)
megyei_adatok.rename(columns=lambda x: re.sub("_arany_", "_arány_", x), inplace=True)
megyei_adatok.rename(columns=lambda x: re.sub(" ", "_", x), inplace=True)
megyei_adatok.rename(columns=lambda x: x.lower(), inplace=True)

In [116]:
list(enumerate(megyei_adatok.columns))

[(0, 'megye'),
 (1, 'lakónépesség_0-14_2001'),
 (2, 'lakónépesség_0-14_2018'),
 (3, 'lakónépesség_15-64_2001'),
 (4, 'lakónépesség_15-64_2018'),
 (5, 'lakónépesség_65-_2001'),
 (6, 'lakónépesség_65-_2018'),
 (7, 'lakónépesség_arány_15-64_0-14_2001'),
 (8, 'lakónépesség_arány_15-64_65-_2001'),
 (9, 'lakónépesség_arány_15-64_0-14_2018'),
 (10, 'lakónépesség_arány_15-64_65-_2018'),
 (11, 'lakónépesség_arány_15-64_65-_arány_2018_2001'),
 (12, 'lakónépesség_15-64_arány_2018_2001'),
 (13, 'lakónépesség_arány_15-64_0-14_arány_2018_2001'),
 (14, 'lakónépesség_0-14_arány_2018_2001'),
 (15, 'lakónépesség_65-_arány_2018_2001'),
 (16, 'népsűrűség_fő_per_km2_2001'),
 (17, 'népsűrűség_fő_per_km2_2018'),
 (18, 'városszám_2001'),
 (19, 'városszám_2018'),
 (20, 'községszám_2001'),
 (21, 'községszám_2018'),
 (22, 'városszám_arány_2018_2001'),
 (23, 'népsűrűség_fő_per_km2_arány_2018_2001'),
 (24, 'községszám_arány_2018_2001'),
 (25, 'élettartam_ffi_2001'),
 (26, 'élettartam_ffi_2017'),
 (27, 'élettartam_

In [117]:
megyei_adatok.to_csv('dataout/megyei_adatok.csv', index=False, header=True)

## Korrelációk

In [124]:
%run definitions.ipynb

In [126]:
megyei_corr = megyei_adatok.corr()
#display(megyei_corr.style.background_gradient(cmap='coolwarm'))
colour_cm(megyei_corr, pwidth=0.25, pheight=0.25)

Loading BokehJS ...